# Association Rules Mining （基础）

### Apriori Algorithm 
    Apriori是用于识别频繁项集的算法。 它采用“自下而上”的方法，首先确定满足最低发生阈值的个别项目。然后扩展项目集合，一次添加一个项目，并检查结果项目集合是否仍然满足指定的阈值。 当没有更多要添加的项目满足最小出现要求时，算法停止。 这里有一个先验行动的例子，假设最小出现阈值为3：

    order 1: apple, egg, milk  
    order 2: carrot, milk  
    order 3: apple, egg, carrot
    order 4: apple, egg
    order 5: apple, carrot
    
    Iteration 1:  统计每个项目发生的次数   
    item set      occurrence count    
    {apple}              4   
    {egg}                3   
    {milk}               2   
    {carrot}             2   

    {milk} and {carrot} 被淘汰，因为它们不符合最低发生的门槛。

    Iteration 2: 使用迭代1中的剩余项目构建大小为2的项目集 (ie: apple, egg)  
    item set           occurence count  
    {apple, egg}             3  

    只剩下{apple，egg}，算法停止，因为没有更多的项目要添加。
   
如果我们有更多的订单和项目，我们可以继续迭代，构建包含2个以上元素的项目集。

### 关联规则挖掘
一旦使用先验生成了项目集，我们就可以开始挖掘关联规则。 本例只查看大小为2的项集，即将生成的关联规则是{A} - > {B}的形式。 这些规则的一个普遍应用是推荐系统的领域，为购买物品A的顾客推荐物品B.

评估关联规则时需要考虑以下三个关键指标：

1. <b>support（支持度）</b>  
     这是包含项目集的订单的百分比。 在上面的例子中，共有5个订单，
     {apple,egg}发生在其中三个，所以：
       
                    support{apple,egg} = 3/5 or 60%
        
     apriori所需的最低支持度阈值可以根据用户所在领域的知识来设置。本例中的
     杂货数据集，因为可能有成千上万个不同的项目和订单可以包含，将支持阈值设置为0.01％可能是合理的。<br>
    
2. <b>confidence（置信度）</b>  
   给定两个项目，A和B，置信度度量项目A、B同时购买占项目A被购买的次数的百分比。 这表示为：
       
                    confidence{A->B} = support{A,B} / support{A}   
                    
    置信度范围从0到1，其中0表示购买A时从不购买B。请注意，置信度是有方向性的。
                    
    在我们的例子中，考虑到购买苹果，鸡蛋被购买的次数的百分比是：
       
                    confidence{apple->egg} = support{apple,egg} / support{apple}
                                           = (3/5) / (4/5)
                                           = 0.75 or 75%
   我们看看相反方向的置信度指标(ie: egg->apple): 
       
                    confidence{egg->apple} = support{apple,egg} / support{egg}
                                           = (3/5) / (3/5)
                                           = 1 or 100%  
                                           
   在这里，我们看到所有包含蛋的订单也包含苹果。但是，这是否意味着这两个项目之间有一个强的关系，还是仅仅偶然发生在同一个订单上？ 为了回答这个问题，我们看看另一个考虑到这两个项目受欢迎程度的度量。<br>  
    
3. <b>lift（提升度）</b>  
    给定两个项目，A和B，提升度表示A和B之间是否存在关系，或者两个项目存在关系是否是偶然发生在一起的（即：随机）。不像其置信度指标可能会根据方向而变化（例如：置信度{A-> B}可能不同于置信度{B-> A}），提升度没有方向。 这意味提升度{A，B}总是等于提升度{B，A}：
       
                    lift{A,B} = lift{B,A} = support{A,B} / (support{A} * support{B})   
    
    本例中，提升度计算如下:
    
                    lift{apple,egg} = lift{egg,apple} = support{apple,egg} / (support{apple} * support{egg})
                                                      = (3/5) / (4/5 * 3/5) 
                                                      = 1.25    
               
    理解提升度的一种方法是将分母想象为A和B如果它们之间不存在关系将以相同订单出现的可能性。 在上面的例子中，如果在80％的订单中发生了苹果，而在60％的订单中发生了蛋，那么如果它们之间没有任何关系，我们希望它们一起出现在48％的时间内（即：80％* 60％）。 另一方面，分子表示苹果和蛋实际上以相同的订单一起出现的频率。 在这个例子中，这是60％的时间。 拿分子除以分母，我们得到苹果和鸡蛋实际上以同样的订单出现了多少次，相比之下，它们之间没有任何关系（即：它们是随机发生的）。    
    
    总结一下，提升度可以采取以下值：
    
     * lift = 1 意味着A和B之间没有关系。（即：A和B只能偶然发生）
      
     * lift > 1 意味着A和B之间有正相关关系。（即：A和B一起发生的次数多于随机）
    
     * lift < 1 意味着A和B之间存在负相关关系。（即：A和B一起发生的次数少于随机）
        
    在我们的例子中，苹果和鸡蛋共同发生1.25倍以上，所以我们得出这样的结论，他们之间正相关。

## Association Rule Mining from Spatial Data for Crime Analysis

### 关联规则分析

In [7]:
import os
import sys
import numpy
import pandas
import matplotlib.pyplot as plt
sys.path.append(os.path.abspath("./util"))
from pymining import itemmining, assocrules  #使用pymining中的关联规则算法

%matplotlib inline
plt.style.use('ggplot')
pandas.set_option('display.max_rows', 10000, "display.max_columns", 100)

#### 从数据集中读取数据

In [8]:
df = pandas.read_csv("./dataset/crimes_census_5poi.csv", index_col=0, sep="\t")
df.shape

(19106, 21)

先了解数据指标

In [9]:
print(df.columns)  

Index(['BLOCKID10', 'First_POI', 'Second_POI', 'Third_POI', 'Fourth_POI',
       'Fifth_POI', 'ARPCIncome', 'ARPerHEdu', 'ARPerWork', 'ARPerRMI5L',
       'ARPer3MU', 'ARPopDen', 'ARPerAA', 'ARHeteInx', 'ARPerM1724',
       'ARPerHOwn', 'ARPerSF', 'NIBRSclass', 'Place2', 'Report_Dat',
       'Street_Nam'],
      dtype='object')


对分析没有价值的字段指标可删去：

BLOCKID10,  # 街区ID   <br>
Street_Nam，# 街道名称 <br>
ARPerRMI5L, # 不满5年租房的人口比例 <br>
ARPer3MU,   # 有3个或多个单元结构的住宅的百分比 <br>
ARHeteInx,  # 种族异质性指数 <br>
ARPerHOwn,  # 拥有家庭的人口比例 <br>
First_POI,  # 第一个最近的POI（信息点），类似： "Second_POI", "Third_POI", "Fourth_POI", "Fifth_POI" <br>

要用到的字段的含义

"ARPCIncome",   # 人均收入; type: real, length 18 <br>
"ARPerHEdu",    # 高中及以上文化程度的比例 <br>
"ARPerWork",    # 受雇人口的百分比 <br>
"ARPopDen",     # 人口密度; type: real, length 18 <br>
"ARPerAA",      # 非洲裔美国人比例 <br>
"ARPerM1724",   # 17-24岁男性的比例 <br>
"ARPerSF",      # 单亲家庭的比例 <br>
"NIBRSclass",   # 犯罪类型 <br>
"Place2",       # 私人住宅，街道/高速公路，等等 <br>
"Report_Dat",   # date <br>

In [10]:
# 删去没有意义的字段
# df = df.drop(["ARPopDen", "ARPerAA", "ARPerM1724", "ARPerSF"], axis=1)
df = df.drop(["BLOCKID10", "Street_Nam", "ARPerRMI5L", "ARPer3MU", "ARHeteInx", "ARPerHOwn"], axis=1)
df = df.drop(["First_POI", "Second_POI", "Third_POI", "Fourth_POI", "Fifth_POI"], axis=1)
#将数据框中记录转换成列表
transactions = [row.tolist() for i, row in df.iterrows()]
print(df.shape)  #发现只留下10个字段
df.describe()    #查看数据分布：unique（取几个不同值）

(19106, 10)


ARPCIncome ARPerHEdu ARPerWork    ARPopDen   ARPerAA  ARPerM1724  \
count       19106     19106     19106       19106     19106       19106   
unique          7         7         7           7         7           7   
top       inc-1/7   edu-6/7  empl-1/7  popden-6/7  afro-1/7  youngm-4/7   
freq         2967      2828      3183        3254      4205        3664   

           ARPerSF                NIBRSclass             Place2 Report_Dat  
count        19106                     19106              19106      19106  
unique           7                        52                 67         36  
top     sinpar-2/7  Theft From Motor Vehicle  Private Residence      07-2x  
freq          3292                      2523               3950        684

In [16]:
df

ARPCIncome ARPerHEdu ARPerWork    ARPopDen   ARPerAA  ARPerM1724  \
0        inc-5/7   edu-7/7  empl-7/7  popden-5/7  afro-1/7  youngm-6/7   
12       inc-4/7   edu-6/7  empl-5/7  popden-4/7  afro-4/7  youngm-5/7   
15       inc-7/7   edu-1/7  empl-7/7  popden-6/7  afro-1/7  youngm-4/7   
17       inc-4/7   edu-3/7  empl-3/7  popden-6/7  afro-3/7  youngm-4/7   
18       inc-1/7   edu-4/7  empl-1/7  popden-7/7  afro-7/7  youngm-5/7   
22       inc-1/7   edu-7/7  empl-1/7  popden-4/7  afro-5/7  youngm-7/7   
23       inc-5/7   edu-7/7  empl-5/7  popden-7/7  afro-3/7  youngm-2/7   
27       inc-3/7   edu-1/7  empl-4/7  popden-3/7  afro-4/7  youngm-4/7   
29       inc-7/7   edu-1/7  empl-7/7  popden-6/7  afro-1/7  youngm-4/7   
31       inc-4/7   edu-5/7  empl-3/7  popden-5/7  afro-3/7  youngm-6/7   
35       inc-5/7   edu-5/7  empl-7/7  popden-7/7  afro-1/7  youngm-5/7   
46       inc-7/7   edu-1/7  empl-7/7  popden-6/7  afro-1/7  youngm-4/7   
47       inc-6/7   edu-7/7  empl-5/7  popden-6/7  afro-1/7  youngm-2/7   
50       inc-5/7   edu-2/7  empl-5/7  popden-3/7  afro-5/7  youngm-1/7   
58       inc-4/7   edu-6/7  empl-6/7  popden-4/7  afro-7/7  youngm-5/7   
63       inc-4/7   edu-3/7  empl-5/7  popden-6/7  afro-4/7  youngm-2/7   
66       inc-4/7   edu-1/7  empl-5/7  popden-5/7  afro-5/7  youngm-7/7   
72       inc-6/7   edu-3/7  empl-5/7  popden-2/7  afro-1/7  youngm-2/7   
76       inc-2/7   edu-5/7  empl-2/7  popden-5/7  afro-5/7  youngm-4/7   
79       inc-6/7   edu-3/7  empl-6/7  popden-4/7  afro-1/7  youngm-1/7   
81       inc-7/7   edu-2/7  empl-5/7  popden-6/7  afro-1/7  youngm-2/7   
86       inc-7/7   edu-2/7  empl-5/7  popden-5/7  afro-1/7  youngm-7/7   
90       inc-5/7   edu-7/7  empl-5/7  popden-1/7  afro-2/7  youngm-3/7   
91       inc-6/7   edu-3/7  empl-7/7  popden-3/7  afro-3/7  youngm-3/7   
100      inc-1/7   edu-6/7  empl-1/7  popden-1/7  afro-6/7  youngm-3/7   
101      inc-3/7   edu-1/7  empl-4/7  popden-3/7  afro-4/7  youngm-4/7   
103      inc-1/7   edu-7/7  empl-1/7  popden-2/7  afro-6/7  youngm-7/7   
105      inc-5/7   edu-7/7  empl-7/7  popden-5/7  afro-1/7  youngm-6/7   
106      inc-2/7   edu-2/7  empl-6/7  popden-1/7  afro-5/7  youngm-5/7   
108      inc-7/7   edu-2/7  empl-5/7  popden-3/7  afro-1/7  youngm-1/7   
109      inc-5/7   edu-5/7  empl-7/7  popden-7/7  afro-6/7  youngm-6/7   
110      inc-4/7   edu-6/7  empl-6/7  popden-3/7  afro-5/7  youngm-5/7   
113      inc-4/7   edu-6/7  empl-5/7  popden-4/7  afro-4/7  youngm-5/7   
116      inc-1/7   edu-7/7  empl-1/7  popden-2/7  afro-6/7  youngm-7/7   
118      inc-3/7   edu-2/7  empl-6/7  popden-3/7  afro-3/7  youngm-7/7   
127      inc-3/7   edu-5/7  empl-3/7  popden-5/7  afro-4/7  youngm-6/7   
129      inc-4/7   edu-6/7  empl-4/7  popden-4/7  afro-4/7  youngm-7/7   
130      inc-7/7   edu-1/7  empl-5/7  popden-4/7  afro-2/7  youngm-1/7   
133      inc-6/7   edu-3/7  empl-7/7  popden-6/7  afro-3/7  youngm-4/7   
137      inc-1/7   edu-7/7  empl-2/7  popden-1/7  afro-6/7  youngm-3/7   
140      inc-5/7   edu-2/7  empl-5/7  popden-7/7  afro-1/7  youngm-1/7   
143      inc-3/7   edu-1/7  empl-4/7  popden-1/7  afro-7/7  youngm-4/7   
145      inc-1/7   edu-6/7  empl-1/7  popden-1/7  afro-6/7  youngm-3/7   
146      inc-2/7   edu-1/7  empl-1/7  popden-6/7  afro-7/7  youngm-3/7   
151      inc-5/7   edu-5/7  empl-7/7  popden-7/7  afro-6/7  youngm-6/7   
152      inc-1/7   edu-7/7  empl-5/7  popden-7/7  afro-2/7  youngm-7/7   
154      inc-5/7   edu-7/7  empl-7/7  popden-5/7  afro-1/7  youngm-6/7   
161      inc-6/7   edu-3/7  empl-6/7  popden-4/7  afro-2/7  youngm-1/7   
164      inc-7/7   edu-4/7  empl-2/7  popden-5/7  afro-3/7  youngm-1/7   
169      inc-6/7   edu-3/7  empl-7/7  popden-3/7  afro-3/7  youngm-3/7   
170      inc-1/7   edu-6/7  empl-1/7  popden-6/7  afro-5/7  youngm-2/7   
176      inc-1/7   edu-6/7  empl-1/7  popden-1/7  afro-6/7  youngm-3/7   
177      inc-3/7   edu-3/7  empl-5/7  popden-7/7  afro-7/7  youngm-2/7   
178      i

In [11]:
#查看转换后的列表中的数据
transactions[:2]

[['inc-5/7',
  'edu-7/7',
  'empl-7/7',
  'popden-5/7',
  'afro-1/7',
  'youngm-6/7',
  'sinpar-6/7',
  'Simple Assault',
  'Apartment/Duplex Private Res',
  '01-0x'],
 ['inc-4/7',
  'edu-6/7',
  'empl-5/7',
  'popden-4/7',
  'afro-4/7',
  'youngm-5/7',
  'sinpar-5/7',
  'Simple Assault',
  'Apartment/Duplex Private Res',
  '01-0x']]

In [6]:
#df.groupby(['ARPCIncome']).count()

#### 产生频繁项集

先定义几个函数

In [17]:
#to_tuple将交易数据转换成元组
to_tuple  = lambda trans_list: tuple([tuple(trans) for trans in trans_list])
# percentage = lambda x, tot=len(transactions): (x * 1.0) / tot

def only_rules_with(columns, dataframe, rules, only_cons=False):
    #按columns对规则rules进行过滤
    list_of_sets = [set(dataframe[column].values) for column in columns]
    result = []
    for rule in rules:
        current_itemset = rule[1] if only_cons else rule[0] | rule[1]
        cond = True
        for column_set in list_of_sets:
            if (current_itemset & column_set) == set():
                cond = False
        if cond:
            result.append(rule)
    return result

def print_that(filepath, rules):
    with open(filepath, 'w+') as result_file:
        for rule in rules:
            result_file.write(rule_to_string(rule))
        
def rule_to_string(rule):
    return str([j for j in rule[0]]) + "  ->  " + str([z for z in rule[1]]) + \
    ", supp: " + str(rule[2]) + \
    ", conf: " + str(rule[3]) + \
    "\n"

In [18]:
min_supp = 70  #支持度计数设为70

#### Relim算法可参见论文： [Paper 1](https://pdfs.semanticscholar.org/cb3e/76d1773d08545f21daf28cc87b051604aa95.pdf) [Paper 2](http://www.borgelt.net/papers/relim.pdf)

In [19]:
%%time
#用pymining中的itemmining算法挖掘频繁项集
#transactions是删除无用字段后数据的列表形式，to_tuple将其转成元组
relim_input = itemmining.get_relim_input(to_tuple(transactions))
relim_itemsets = itemmining.relim(relim_input, min_support=min_supp) #获得频繁项集
print("number of frequent itemsets", len(relim_itemsets), "\n")                        

number of frequent itemsets 17164 

CPU times: user 3.59 s, sys: 94.8 ms, total: 3.69 s
Wall time: 3.72 s


In [10]:
list(relim_itemsets)[:10] #查看部分频繁项集

[frozenset({'Private Residence', 'edu-4/7', 'youngm-6/7'}),
 frozenset({'Burglary/B&E', 'sinpar-7/7', 'youngm-3/7'}),
 frozenset({'Credit Card/Teller Fraud', 'afro-1/7'}),
 frozenset({'Shoplifting', 'afro-2/7', 'popden-2/7'}),
 frozenset({'Apartment/Duplex Private Res',
            'empl-3/7',
            'popden-5/7',
            'sinpar-6/7'}),
 frozenset({'Apartment/Duplex Private Res', 'afro-3/7', 'edu-3/7'}),
 frozenset({'Theft From Motor Vehicle',
            'afro-7/7',
            'empl-3/7',
            'popden-5/7',
            'sinpar-6/7',
            'youngm-6/7'}),
 frozenset({'Hotel/Motel', 'edu-1/7', 'youngm-4/7'}),
 frozenset({'Apartment/Duplex Private Res',
            'empl-5/7',
            'inc-2/7',
            'youngm-2/7'}),
 frozenset({'All Other Thefts', 'afro-6/7', 'edu-7/7', 'empl-1/7'})]

### 关联规则生成

In [12]:
min_conf = 0.60  #置信度设为60%

In [13]:
%%time
rules = assocrules.mine_assoc_rules(relim_itemsets, min_support=min_supp, min_confidence=min_conf)
print(len(rules))  

102486
Wall time: 1.76 s


In [15]:
rules[:3]  #查看部分生成的规则

[(frozenset({'Department Store',
             'Shoplifting',
             'afro-1/7',
             'edu-4/7',
             'empl-6/7',
             'inc-6/7',
             'popden-1/7',
             'youngm-1/7'}),
  frozenset({'sinpar-3/7'}),
  78,
  1.0),
 (frozenset({'Department Store',
             'Shoplifting',
             'afro-1/7',
             'edu-4/7',
             'empl-6/7',
             'inc-6/7',
             'popden-1/7'}),
  frozenset({'sinpar-3/7', 'youngm-1/7'}),
  78,
  1.0),
 (frozenset({'Shoplifting',
             'afro-1/7',
             'edu-4/7',
             'empl-6/7',
             'inc-6/7',
             'popden-1/7'}),
  frozenset({'Department Store', 'sinpar-3/7', 'youngm-1/7'}),
  78,
  0.65)]

#### 规则过滤
只留下有犯罪或有犯罪后果的规则（RHS）

In [16]:
#用自定义的only_rules_with函数进行规则过滤
rules_with_crimes = only_rules_with(["NIBRSclass"], df, rules)
print("# of rules with crimes:", len(rules_with_crimes))
rules_with_crimes_in_cons = only_rules_with(["NIBRSclass"], df, rules, only_cons=True)
print("# of rules with crimes in consequent:", len(rules_with_crimes_in_cons))

# of rules with crimes: 23789
# of rules with crimes in consequent: 2086


In [17]:
# 输出一些规则
for rule in rules_with_crimes_in_cons[:20]:
    print(rule_to_string(rule))

['popden-1/7', 'inc-6/7', 'Department Store']  ->  ['sinpar-3/7', 'youngm-1/7', 'edu-4/7', 'Shoplifting', 'empl-6/7', 'afro-1/7'], supp: 78, conf: 0.8387096774193549

['popden-1/7', 'Department Store']  ->  ['sinpar-3/7', 'youngm-1/7', 'afro-1/7', 'edu-4/7', 'Shoplifting', 'inc-6/7', 'empl-6/7'], supp: 78, conf: 0.8041237113402062

['popden-1/7', 'Department Store', 'inc-6/7', 'empl-6/7']  ->  ['edu-4/7', 'sinpar-3/7', 'Shoplifting', 'youngm-1/7', 'afro-1/7'], supp: 78, conf: 0.8387096774193549

['popden-1/7', 'empl-6/7', 'Department Store']  ->  ['sinpar-3/7', 'youngm-1/7', 'edu-4/7', 'Shoplifting', 'inc-6/7', 'afro-1/7'], supp: 78, conf: 0.8387096774193549

['afro-1/7', 'empl-6/7', 'Department Store', 'popden-1/7', 'inc-6/7']  ->  ['edu-4/7', 'sinpar-3/7', 'youngm-1/7', 'Shoplifting'], supp: 78, conf: 0.8387096774193549

['popden-1/7', 'Department Store', 'afro-1/7', 'inc-6/7']  ->  ['edu-4/7', 'sinpar-3/7', 'youngm-1/7', 'Shoplifting', 'empl-6/7'], supp: 78, conf: 0.8387096774193549

In [16]:
# 将规则保存到文件中
# print_that('./dataset/result_file.txt', rules_with_crimes)
# print_that('./dataset/result_file_only_cons.txt', rules_with_crimes_in_cons)

### 评估
提升度：Lift(X->Y)=Confidence(X->Y)/Support(Y) <br>
规则的提升度的意义在于度量项集{X}和项集{Y}的独立性。即，Lift(X->Y)= 1 表面 {X}，{Y}相互独立。[注：P(XY)=P(X)*P(Y),if X is independent of Y] <br>
如果该值=1,说明两个条件没有任何关联,如果<1,说明A条件(或者说A事件的发生)与B事件是相斥的,一般在数据挖掘中当提升度大于3时,我们才承认挖掘出的关联规则是有价值的。

出错率:Conviction(X->Y)=(1-Support(Y))/(1-Confidence(X->Y)) <br>
Conviction的意义在于度量规则预测错误的概率。表示X出现而Y不出现的概率。

In [17]:
def lift(rule_supp, ant_supp, cons_supp):
    #ant_supp,前项支持度；cons_supp，后项支持度；rule_supp，规则支持度
    return (rule_supp / 1.0) / (ant_supp * cons_supp)

def conviction(cons_supp, rule_conf):
    #cons_supp，后项支持度；rule_conf，规则置信度
    return (1.0 - cons_supp) / (1.0 - rule_conf)

In [18]:
for rule in rules:
    l = lift(relim_itemsets[rule[0] | rule[1]], relim_itemsets[rule[0]], relim_itemsets[rule[1]])
    if l > 1:
        print(l)
    #c = conviction(relim_itemsets[rule[1]], rule[3])

#### 用一条规则，了解评估指标计算过程

In [19]:
rule=rules[0]
rule[0],rule[1]

(frozenset({'Department Store',
            'Shoplifting',
            'afro-1/7',
            'edu-4/7',
            'inc-6/7',
            'popden-1/7',
            'sinpar-3/7',
            'youngm-1/7'}),
 frozenset({'empl-6/7'}))

In [20]:
relim_itemsets[rule[0] | rule[1]]

78

In [21]:
relim_itemsets[rule[0]]

78

In [22]:
relim_itemsets[rule[1]]

2643

In [23]:
lift(relim_itemsets[rule[0] | rule[1]], relim_itemsets[rule[0]], relim_itemsets[rule[1]])

0.00037835792659856227